## Dynamic plot - showing all wildfires yearly

GOAL: Creating a plot with dynamic visualizations of yearly wildfires  in the us


In [1]:
import time
import pandas as pd
import numpy as np
import sqlite3
import os
from datetime import date, timedelta
import datetime
import shapefile as shp
import matplotlib.pyplot as plt
import seaborn as sns
import shapefile
import geopandas as gpd
from bokeh.models import *
from bokeh.plotting import *
from bokeh.io import *
from bokeh.tile_providers import *
from bokeh.palettes import *
from bokeh.transform import *
from bokeh.layouts import *
from scripts import *

In [2]:
# establishing db connection

con = sqlite3.connect("FPA_FOD_20170508.sqlite")

In [3]:
# reading data from database

all_fires = pd.read_sql_query("""SELECT STATE, COUNTY, FIRE_YEAR, FIRE_SIZE,FIRE_SIZE_CLASS, LATITUDE, LONGITUDE,
date(DISCOVERY_DATE) as DISCOVERY_DATE,date(CONT_DATE) as CONT_DATE
FROM Fires
ORDER BY FIRE_SIZE DESC
""", con)

In [4]:
# mapping fire size class to numerical values
all_fires["size_class"] = all_fires["FIRE_SIZE_CLASS"].map({"A":0.2,"B":0.5,"C":1,"D":2,"E":4,"F":8,"G":16})

In [6]:
# creating geodataframe
gdf_all = geodf_create_transform(all_fires,"LONGITUDE","LATITUDE","size_class",0.0005)

C:\Users\szklarnia\Desktop\datascience\projekty\us wildfires\scripts.py:62: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gdf.x_crds[i] = list(gdf.geometry[i].coords)[0][0]
C:\Users\szklarnia\Desktop\datascience\projekty\us wildfires\scripts.py:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gdf.y_crds[i] = list(gdf.geometry[i].coords)[0][1]


In [18]:
gdf_all["size_class"] = gdf_all["size_class"]/1.5

In [7]:
# specyfying map range
x_range,y_range = get_max_min(-170,-70,70,20)


In [ ]:
# creating dynamic plot
years = np.arange(1992,2016,1)

# specyfying source
source = ColumnDataSource(gdf_all.drop("geometry",axis=1)[gdf_all.FIRE_YEAR == 1992])
# creating plot
p = plot_bubble_map_for_animation(df=gdf_all,
                source=source,
                radius_col="size_class",
                hover_tuples=[("Size [in acres]:","@FIRE_SIZE"),("Discovered:","@DISCOVERY_DATE"),("Contained:","@CONT_DATE")],
                x_range=x_range,
                y_range=y_range,
                title = f"US wildfires in 1992",
                leg_label = "Wildfires by size")

# creating handle object
output_notebook()
handle = show(p, notebook_handle = True)

# updating plot yearly
for year in years:
    # specyfying dataframe, changing title
    df = gdf_all[gdf_all.FIRE_YEAR == year].drop("geometry",axis=1)
    p.title.text = f"Wildfires in california in {year}"
    # Push new data
    source.stream(df)
    # Purge old data
    source.data = df
    push_notebook(handle=handle)
    export_png(p, filename=f"plot_{year}.png")
    time.sleep(2)

Loading BokehJS ...